#Data extraction

In [3]:
import fitz  # PyMuPDF
import pdfplumber
from langchain.text_splitter import CharacterTextSplitter
import os
from pathlib import Path
#[[metadatv1, valuesve],[metadatav2, valuev2]]

def extract_text_and_images(pdf_path):
    """
    Extract text and images from a PDF file.
    pdf_path: Path to the PDF file
    """
    doc = fitz.open(pdf_path)
    filename = Path(pdf_path).stem
    texts = []
    images = []
    text_metadata = []
    image_metadata = []
    
    for page_num in range(len(doc)):
        page = doc.load_page(page_num)
        page_text = page.get_text("text")
        texts.append(page_text)
        text_metadata.append({
            "source_file": pdf_path,
            "page_number": page_num + 1,
            "chunk_size": len(page_text)
        })
        
        # Extract images
        for img_index, img in enumerate(page.get_images(full=True)):
            xref = img[0]
            base_image = doc.extract_image(xref)
            image_bytes = base_image["image"]
            image_ext = base_image["ext"]
            image_name = f"image_page{page_num+1}_{img_index}_{filename}.{image_ext}"
            images.append((image_name, image_bytes, page_num + 1))
            image_metadata.append({
                "source_file": pdf_path,
                "page_number": page_num + 1,
                "image_name": image_name
            })
            
            # Optionally, save the image
            with open(os.path.join("static", image_name), "wb") as image_file:
                image_file.write(image_bytes)
    
    return texts, images, text_metadata, image_metadata

def extract_tables(pdf_path):
    """
    Extract tables from a PDF file.
    pdf_path: Path to the PDF file
    """
    tables = []
    table_metadata = []
    
    with pdfplumber.open(pdf_path) as pdf:
        for page_num, page in enumerate(pdf.pages):
            extracted_tables = page.extract_tables()
            for table in extracted_tables:
                tables.append(table)
                table_metadata.append({
                    "source_file": pdf_path,
                    "page_number": page_num + 1,
                    "table_size": len(table)
                })
    
    return tables, table_metadata

def categorize_elements(texts, tables, images):
    """
    Categorize extracted elements from a PDF into texts, tables, and images.
    """
    return texts, tables, images

def process_pdfs_in_directory(directory_path):
    """
    Process all PDF files in the specified directory.
    directory_path: Path to the directory containing PDF files
    """
    # Ensure 'static' directory exists to save images
    os.makedirs("static", exist_ok=True)

    pdf_data = []

    for filename in os.listdir(directory_path):
        if filename.endswith(".pdf"):
            pdf_path = os.path.join(directory_path, filename)
            print(f"Processing {filename}...")

            # Extract data from the PDF
            raw_texts, raw_images, text_metadata, image_metadata = extract_text_and_images(pdf_path)
            raw_tables, table_metadata = extract_tables(pdf_path)
            texts, tables, images = categorize_elements(raw_texts, raw_tables, raw_images)



            # Store the extracted data in a dictionary
            pdf_data.append({
                "filename": filename,
                "texts": texts,
                "tables": tables,
                "images": [image[0] for image in images],
                "text_metadata": text_metadata,
                "table_metadata": table_metadata,
                "image_metadata": image_metadata
            })

    return pdf_data, texts, tables

# Directory path
directory_path = "/Users/dhvani/Desktop/blossombot/"

# Process all PDFs in the directory
pdf_data, texts, tables = process_pdfs_in_directory(directory_path)

# Print or return the extracted data
for data in pdf_data:
    
    print(f"Filename: {data['filename']}")
    print("Texts:", data['texts'])
    print("Text Metadata:", data['text_metadata'])
    print("Tables:", data['tables'])
    print("Table Metadata:", data['table_metadata'])
    print("Images:", data['images'])
    print("Image Metadata:", data['image_metadata'])

Processing Womens.pdf...
Filename: Womens.pdf
Texts: ['NATIONAL HUMAN RIGHTS COMMISSION\nWomen’s Right to Health\nN. B. Sarojini & others\n', "Contributed by\nN. B. Sarojini\nSuchita Chakraborty\nDeepa Venkatachalam\nSaswati Bhattacharya\nAnuj Kapilashrami\nRanjan De\nWith support from\nBeenu Rawat\nPreeti Nayak\nManjeer Mukherjee\nNATIONAL HUMAN RIGHTS COMMISSION\nFaridkot House, Copernicus Marg\nNew Delhi 110 001, India\nWomen's Right to Health\n", 'Designed and printed by Rajika Press Services Pvt. Ltd\nThe views expressed by the authors in this publication\nare not necessarily the views of the NHRC.\nNATIONAL HUMAN RIGHTS COMMISSION\nFaridkot House, Copernicus Marg\nNew Delhi 110 001, India\nTel: 23383570 Fax: 23384863\nE-mail: covdnhrc@nic.in\nWebsite: www.nhrc.nic.in\n© 2006, National Human Rights Commission\n', 'Introduction\n9\nHealthcare System in India – A Critical Analysis\n11\nAn Overview of Women’s Health Status in India\n33\nRight to Health and the Women’s Movement\n49\nN

In [6]:
data['text_metadata']

[{'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf',
  'page_number': 1,
  'chunk_size': 81},
 {'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf',
  'page_number': 2,
  'chunk_size': 294},
 {'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf',
  'page_number': 3,
  'chunk_size': 361},
 {'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf',
  'page_number': 4,
  'chunk_size': 376},
 {'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf',
  'page_number': 5,
  'chunk_size': 0},
 {'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf',
  'page_number': 6,
  'chunk_size': 2101},
 {'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf',
  'page_number': 7,
  'chunk_size': 1958},
 {'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf',
  'page_number': 8,
  'chunk_size': 1885},
 {'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf',
  'page_number': 9,
  'chunk_size': 293},
 {'source_file': '/Users/dhvani/Desktop/blosso

: 

In [259]:
# Print the resulting chunks
text_chunk_list=[]
for i, chunk in enumerate(texts):
    text_chunk_list.append(chunk)
    print(f"Chunk {i + 1}:\n{chunk}\n")

Chunk 1:
NATIONAL HUMAN RIGHTS COMMISSION
Women’s Right to Health
N. B. Sarojini & others


Chunk 2:
Contributed by
N. B. Sarojini
Suchita Chakraborty
Deepa Venkatachalam
Saswati Bhattacharya
Anuj Kapilashrami
Ranjan De
With support from
Beenu Rawat
Preeti Nayak
Manjeer Mukherjee
NATIONAL HUMAN RIGHTS COMMISSION
Faridkot House, Copernicus Marg
New Delhi 110 001, India
Women's Right to Health


Chunk 3:
Designed and printed by Rajika Press Services Pvt. Ltd
The views expressed by the authors in this publication
are not necessarily the views of the NHRC.
NATIONAL HUMAN RIGHTS COMMISSION
Faridkot House, Copernicus Marg
New Delhi 110 001, India
Tel: 23383570 Fax: 23384863
E-mail: covdnhrc@nic.in
Website: www.nhrc.nic.in
© 2006, National Human Rights Commission


Chunk 4:
Introduction
9
Healthcare System in India – A Critical Analysis
11
An Overview of Women’s Health Status in India
33
Right to Health and the Women’s Movement
49
National and International Remedies for Women’s Right to Healt

In [260]:
len(text_chunk_list)

145

using tapas for table summarization

In [261]:
from transformers import PegasusForConditionalGeneration, PegasusTokenizer, TapasTokenizer, TapasForQuestionAnswering
import openai
import os
import logging
import pandas as pd

# Set up logging
logging.basicConfig(level=logging.INFO)
logger = logging.getLogger(__name__)

# Set your OpenAI API key and base URL if necessary
openai.api_key = os.getenv("OPENAI_API_KEY")
# Optional base URL configuration if you have a custom endpoint
# openai.api_base = "https://..."

# Initialize Pegasus model and tokenizer
pegasus_model = PegasusForConditionalGeneration.from_pretrained('google/pegasus-xsum')
pegasus_tokenizer = PegasusTokenizer.from_pretrained('google/pegasus-xsum')

# Initialize TAPAS model and tokenizer
tapas_model = TapasForQuestionAnswering.from_pretrained('google/tapas-large-finetuned-wtq')
tapas_tokenizer = TapasTokenizer.from_pretrained('google/tapas-large-finetuned-wtq')

# Function to summarize texts using Pegasus

def summarize2(text):
    print(text)
    tokens = pegasus_tokenizer(text, truncation=True, padding='longest', return_tensors="pt")
    summary_ids = pegasus_model.generate(tokens['input_ids'], max_length=50, min_length=30, length_penalty=2.0, num_beams=4, early_stopping=True)
    return pegasus_tokenizer.decode(summary_ids[0], skip_special_tokens=True)

# Function to generate questions and answers from tables using TAPAS
def generate_table_qa_with_tapas(tables):
    """
    Generate Q&A from table elements using TAPAS
    tables: List of lists (tables in nested list format)
    """
    def generate_qa(table):
        try:
            # Convert the nested list to a pandas dataframe and fill None values with empty strings
            df = pd.DataFrame(table[1:], columns=table[0]).fillna('')
            logger.info(f"DataFrame:\n{df}")

            # List of questions to generate insights from the table
            questions = [
                "What is the summary of this table?",
                "What are the key findings?",
                "What are the highest values in each category?",
                "What are the lowest values in each category?"
            ]

            qa_results = []
            for question in questions:
                inputs = tapas_tokenizer(table=df, queries=[question], padding='max_length', return_tensors="pt")
                logger.info(f"Inputs: {inputs}")

                outputs = tapas_model(**inputs)
                logger.info(f"Outputs: {outputs}")

                predicted_answer_coordinates, predicted_aggregation_indices = tapas_tokenizer.convert_logits_to_predictions(
                    inputs,
                    outputs.logits.detach(),
                    outputs.logits_aggregation.detach()
                )
                logger.info(f"Predicted Coordinates: {predicted_answer_coordinates}")

                # Extract the predicted answer text
                answers = []
                for coordinates in predicted_answer_coordinates[0]:
                    if coordinates:
                        cell_value = df.iat[coordinates[0], coordinates[1]]
                        answers.append(cell_value)
                
                qa_results.append(f"Q: {question} A: {'; '.join(answers)}")

            return "\n".join(qa_results)
        except Exception as e:
            logger.error(f"Error generating Q&A from table: {e}")
            return "Error generating Q&A from table."

    return [generate_qa(table) for table in tables]

# Function to generate summaries
def generate_text_summaries(text_chunks=None, tables=None, summarize_texts_flag=False):
    """
    Summarize text and table elements
    text_chunks: List of text chunks
    tables: List of lists (tables in nested list format)
    summarize_texts_flag: Bool to summarize texts
    """
    text_summaries = []
    table_summaries = []

    # Summarize each text chunk if requested
    if text_chunks and summarize_texts_flag:
        #text_summaries = summarize_texts_with_pegasus(text_chunks)
        text_summaries = [summarize2(text) for text in text_chunks]
    elif text_chunks:
        text_summaries = text_chunks

    # Generate Q&A from tables
    if tables:
        table_summaries = generate_table_qa_with_tapas(tables)

    return text_summaries, table_summaries

Some weights of PegasusForConditionalGeneration were not initialized from the model checkpoint at google/pegasus-xsum and are newly initialized: ['model.decoder.embed_positions.weight', 'model.encoder.embed_positions.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [262]:
# Generate summaries
text_summaries, table_summaries = generate_text_summaries(text_chunks=text_chunk_list, tables=tables, summarize_texts_flag=True)

print("Text Summaries:")
for i, summary in enumerate(text_summaries):
    print(f"Summary {i + 1}:\n{summary}\n")

print("Table Summaries:")
for i, summary in enumerate(table_summaries):
    print(f"Summary {i + 1}:\n{summary}\n")

NATIONAL HUMAN RIGHTS COMMISSION
Women’s Right to Health
N. B. Sarojini & others

Contributed by
N. B. Sarojini
Suchita Chakraborty
Deepa Venkatachalam
Saswati Bhattacharya
Anuj Kapilashrami
Ranjan De
With support from
Beenu Rawat
Preeti Nayak
Manjeer Mukherjee
NATIONAL HUMAN RIGHTS COMMISSION
Faridkot House, Copernicus Marg
New Delhi 110 001, India
Women's Right to Health

Designed and printed by Rajika Press Services Pvt. Ltd
The views expressed by the authors in this publication
are not necessarily the views of the NHRC.
NATIONAL HUMAN RIGHTS COMMISSION
Faridkot House, Copernicus Marg
New Delhi 110 001, India
Tel: 23383570 Fax: 23384863
E-mail: covdnhrc@nic.in
Website: www.nhrc.nic.in
© 2006, National Human Rights Commission

Introduction
9
Healthcare System in India – A Critical Analysis
11
An Overview of Women’s Health Status in India
33
Right to Health and the Women’s Movement
49
National and International Remedies for Women’s Right to Health
83
Strategies and Actions
103
Check Y

INFO:__main__:DataFrame:
                          None
0                             
1                             
2      N. B. Sarojini & others
3                             
ERROR:__main__:Error generating Q&A from table: expected string or bytes-like object, got 'NoneType'
INFO:__main__:DataFrame:
Empty DataFrame
Columns: [, , ]
Index: []
INFO:__main__:Inputs: {'input_ids': tensor([[  101,  2054,  2003,  1996, 12654,  1997,  2023,  2795,  1029,   102,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0

Text Summaries:
Summary 1:
The National Commission for Women (NCW) has called for a meeting to discuss the issue of women’s right to health, in the wake of the rape and murder of a young woman by a police officer in the capital, Delhi

Summary 2:
The World Health Organization (WHO) and the United Nations Children's Fund (Unicef) are working together to improve the health of women and children in India.

Summary 3:
This publication is published by the National Human Rights Commission (NHRC) in collaboration with the Indian Council of Social Research (ICSR) and the National Commission for Human Rights (NCHR).

Summary 4:
This paper is part of a series of papers on women’s health published by the United Nations Population Fund (Unicef) and the World Health Organization (WHO).

Summary 5:
A selection of photos from across the African continent this week, courtesy of AFP, AP, EPA, Reuters and Reuters news agencies and Reuters news agency.

Summary 6:
The National Human Rights Commission of 

In [263]:
table_summaries

['Error generating Q&A from table.',
 'Error generating Q&A from table.',
 'Error generating Q&A from table.',
 'Error generating Q&A from table.',
 'Q: What is the summary of this table? A: Manual Agricultural Workers:\nPostural problems; exposure\nto dusts and chemicals; un-\nguarded implements; working\nbarefoot.; Quarry Workers (chrome):\nExposure to high tempera-\ntures; lack of eye protection.\nQ: What are the key findings? A: Manual Agricultural Workers:\nPostural problems; exposure\nto dusts and chemicals; un-\nguarded implements; working\nbarefoot.; Quarry Workers (chrome):\nExposure to high tempera-\ntures; lack of eye protection.\nQ: What are the highest values in each category? A: \nQ: What are the lowest values in each category? A: Quarry Workers (chrome):\nExposure to high tempera-\ntures; lack of eye protection.',
 'Q: What is the summary of this table? A: Ready-made Garments\nworkers: Postural problems;\nheavy workload.; Home based house workers:\nExposure to dust, fume

In [264]:
# Output results
for i, summary in enumerate(text_summaries):
    print(f"Text Summary {i+1}:\n{summary}\n")
"""
for i, summary in enumerate(table_summaries):
    print(f"Table Summary {i+1}:\n{summary}\n")
"""

Text Summary 1:
The National Commission for Women (NCW) has called for a meeting to discuss the issue of women’s right to health, in the wake of the rape and murder of a young woman by a police officer in the capital, Delhi

Text Summary 2:
The World Health Organization (WHO) and the United Nations Children's Fund (Unicef) are working together to improve the health of women and children in India.

Text Summary 3:
This publication is published by the National Human Rights Commission (NHRC) in collaboration with the Indian Council of Social Research (ICSR) and the National Commission for Human Rights (NCHR).

Text Summary 4:
This paper is part of a series of papers on women’s health published by the United Nations Population Fund (Unicef) and the World Health Organization (WHO).

Text Summary 5:
A selection of photos from across the African continent this week, courtesy of AFP, AP, EPA, Reuters and Reuters news agencies and Reuters news agency.

Text Summary 6:
The National Human Rights 

'\nfor i, summary in enumerate(table_summaries):\n    print(f"Table Summary {i+1}:\n{summary}\n")\n'

In [265]:
text_summaries

['The National Commission for Women (NCW) has called for a meeting to discuss the issue of women’s right to health, in the wake of the rape and murder of a young woman by a police officer in the capital, Delhi',
 "The World Health Organization (WHO) and the United Nations Children's Fund (Unicef) are working together to improve the health of women and children in India.",
 'This publication is published by the National Human Rights Commission (NHRC) in collaboration with the Indian Council of Social Research (ICSR) and the National Commission for Human Rights (NCHR).',
 'This paper is part of a series of papers on women’s health published by the United Nations Population Fund (Unicef) and the World Health Organization (WHO).',
 'A selection of photos from across the African continent this week, courtesy of AFP, AP, EPA, Reuters and Reuters news agencies and Reuters news agency.',
 'The National Human Rights Commission of India (NHRC) has released the following statement on the World Da

IMAGE SUMMARIZATION

In [266]:
import base64
from transformers import TrOCRProcessor, VisionEncoderDecoderModel
from PIL import Image
import requests
import os
from langchain_core.messages import HumanMessage

# Function to encode image
def encode_image(image_path):
    with open(image_path, "rb") as image_file:
        return base64.b64encode(image_file.read()).decode("utf-8")

# Function to summarize image using OCR model
def image_summarize(image_path, ocr_processor, ocr_model, prompt):
    image = Image.open(image_path).convert("RGB")
    pixel_values = ocr_processor(images=image, return_tensors="pt").pixel_values
    generated_ids = ocr_model.generate(pixel_values)
    generated_text = ocr_processor.batch_decode(generated_ids, skip_special_tokens=True)[0]

    # You may adjust this part based on how you want to format your summary
    summary = f"{prompt}\n\n{generated_text}"
    return summary

# Function to generate image summaries
def generate_img_summaries(path, ocr_processor, ocr_model, prompt):
    img_base64_list = []
    image_summaries = []

    for img_file in sorted(os.listdir(path)):
        if img_file.endswith(".png") or img_file.endswith(".jpeg"):  # Adjust file extension as needed
            img_path = os.path.join(path, img_file)
            try:
                base64_image = encode_image(img_path)
                img_base64_list.append(base64_image)
                summary = image_summarize(img_path, ocr_processor, ocr_model, prompt)
                image_summaries.append(summary)
            except Exception as e:
                print(f"Error processing image {img_file}: {e}")

    return img_base64_list, image_summaries

# Prompt
prompt = """You are an assistant tasked with summarizing images for retrieval. \
These summaries will be embedded and used to retrieve the raw image. \
Give a concise summary of the image that is well optimized for retrieval."""

# Load OCR processor and model
ocr_processor = TrOCRProcessor.from_pretrained('microsoft/trocr-base-handwritten')
ocr_model = VisionEncoderDecoderModel.from_pretrained('microsoft/trocr-base-handwritten')

# Path to the directory containing images
path_to_images = "static/"

# Generate image summaries
img_base64_list, image_summaries = generate_img_summaries(path_to_images, ocr_processor, ocr_model, prompt)


Some weights of VisionEncoderDecoderModel were not initialized from the model checkpoint at microsoft/trocr-base-handwritten and are newly initialized: ['encoder.pooler.dense.bias', 'encoder.pooler.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/Users/dhvani/Desktop/blossombot/.venv/lib/python3.11/site-packages/transformers/generation/utils.py:1168: UserWarning: Using the model-agnostic default `max_length` (=20) to control the generation length. We recommend setting `max_new_tokens` to control the maximum length of the generation.
  warnings.warn(


In [267]:
image_summaries

['You are an assistant tasked with summarizing images for retrieval. These summaries will be embedded and used to retrieve the raw image. Give a concise summary of the image that is well optimized for retrieval.\n\n0 2',
 'You are an assistant tasked with summarizing images for retrieval. These summaries will be embedded and used to retrieve the raw image. Give a concise summary of the image that is well optimized for retrieval.\n\nRio',
 'You are an assistant tasked with summarizing images for retrieval. These summaries will be embedded and used to retrieve the raw image. Give a concise summary of the image that is well optimized for retrieval.\n\n0 2',
 'You are an assistant tasked with summarizing images for retrieval. These summaries will be embedded and used to retrieve the raw image. Give a concise summary of the image that is well optimized for retrieval.\n\n2 9',
 'You are an assistant tasked with summarizing images for retrieval. These summaries will be embedded and used to re

In [268]:
import os
os.environ['OPENAI_API_KEY'] = 'sk-proj-aTsOTCUlbnxYqFxHd9d5T3BlbkFJ9hNfpTKUau94QJKD9ils'

In [269]:
from pinecone import Pinecone, ServerlessSpec

pc = Pinecone(api_key="6ab49224-b6f2-4358-8430-28b8af6fcde3")

In [275]:
index_name = "blossombot5"

if index_name not in pc.list_indexes().names():
    pc.create_index(
        name=index_name,
        dimension=768,
        metric="cosine",
        spec=ServerlessSpec(
            cloud='aws', 
            region='us-east-1'
        ) 
    ) 

In [276]:
index = pc.Index(index_name)


uploading text on vectorstore

In [277]:

from sentence_transformers import SentenceTransformer
# Initialize the model
model = SentenceTransformer('bert-base-nli-mean-tokens')

def get_embedding(text):
    try:
        embedding = model.encode(text)
        return embedding
    except Exception as e:
        logger.error(f"Error generating embedding for text: {text}. Error: {e}")
        return None

text_embedding = []

for i in text_chunk_list:
    print(i)
    text_embedding.append(get_embedding(i))

    

INFO:sentence_transformers.SentenceTransformer:Use pytorch device_name: mps
INFO:sentence_transformers.SentenceTransformer:Load pretrained SentenceTransformer: bert-base-nli-mean-tokens
/Users/dhvani/Desktop/blossombot/.venv/lib/python3.11/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


NATIONAL HUMAN RIGHTS COMMISSION
Women’s Right to Health
N. B. Sarojini & others



Batches: 100%|██████████| 1/1 [00:00<00:00,  2.14it/s]


Contributed by
N. B. Sarojini
Suchita Chakraborty
Deepa Venkatachalam
Saswati Bhattacharya
Anuj Kapilashrami
Ranjan De
With support from
Beenu Rawat
Preeti Nayak
Manjeer Mukherjee
NATIONAL HUMAN RIGHTS COMMISSION
Faridkot House, Copernicus Marg
New Delhi 110 001, India
Women's Right to Health



Batches: 100%|██████████| 1/1 [00:00<00:00, 10.03it/s]


...

Batches: 100%|██████████| 1/1 [00:00<00:00, 86.33it/s]


143
The dossier has been prepared by Sama - Resource Group
for Women and Health, a Delhi-based women’s group, which
primarily works on health issues and issues related to women,
especially from marginalised communities.
Sama is an active member of Jan Swasthya Abhiyan (Indian
Chapter of People’s Health Movement), and is part of the
National Coordination Committee (NCC) of National Autono-
mous Women’s Conference.



Batches: 100%|██████████| 1/1 [00:00<00:00, 72.45it/s]


NATIONAL HUMAN RIGHTS COMMISSION
Faridkot House, Copernicus Marg
New Delhi 110 001, India
T
el: 23385368 Fax: 23384863
E-mail: covdnhrc@nic.in
Website: www.nhrc.nic.in



Batches: 100%|██████████| 1/1 [00:00<00:00, 39.78it/s]


In [278]:
text_metadata_lst = []
for i, text in enumerate(data['texts']):
    text_metadata = data['text_metadata'][i]
    text_metadata_lst.append(text_metadata)
    print(text_metadata)

{'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf', 'page_number': 1, 'chunk_size': 81}
{'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf', 'page_number': 2, 'chunk_size': 294}
{'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf', 'page_number': 3, 'chunk_size': 361}
{'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf', 'page_number': 4, 'chunk_size': 376}
{'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf', 'page_number': 5, 'chunk_size': 0}
{'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf', 'page_number': 6, 'chunk_size': 2101}
{'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf', 'page_number': 7, 'chunk_size': 1958}
{'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf', 'page_number': 8, 'chunk_size': 1885}
{'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf', 'page_number': 9, 'chunk_size': 293}
{'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf', 'page_number': 10, 'chunk_size': 2566

In [279]:
len(text_metadata_lst)

145

In [280]:
for i in range(len(text_metadata_lst)):
    if text_embedding[i] is not None:
        print(text_embedding[i])
        try:
            response = index.upsert(
                vectors=[
                    {
                        'id': f"text_{i}",
                        'values': text_embedding[i].tolist(),
                        'metadata': {**text_metadata_lst[i], 'original_text': text_chunk_list[i]}  # Add original text to metadata
                    }
                ]
            )
            logger.info(f"Upsert response: {response}")
            
        except Exception as e:
            logger.error(f"Error upserting text data for ")
    else:
        logger.warning(f"Embedding for text on page is None")

[ 4.71695304e-01  1.97417647e-01  4.74661868e-03 -6.76839724e-02
  4.53341126e-01  1.91338100e-02  6.63943172e-01 -5.66610754e-01
 -3.22602898e-01 -1.47070438e-01  7.45022476e-01  6.17788255e-01
  3.84501040e-01  1.02253306e+00 -4.76349235e-01  5.20720959e-01
 -4.26309168e-01  3.26837488e-02  3.55543895e-03 -2.04443336e-01
 -4.45711493e-01 -4.03121680e-01  4.83097166e-01  3.22541744e-01
  8.30778778e-01  1.32145381e+00  2.04397440e-02 -4.23702151e-01
 -5.99022448e-01  3.97891641e-01  2.35097796e-01 -2.83592850e-01
 -5.23861408e-01  6.07923381e-02  1.11500931e+00  4.29922909e-01
  5.08429036e-02  8.70739877e-01  7.06631094e-02 -7.03941524e-01
 -5.03930867e-01 -7.78101146e-01  2.83467829e-01  8.55517507e-01
 -5.62443674e-01 -2.30032042e-01 -6.99534237e-01  9.18634892e-01
  1.59409359e-01  1.17735587e-01 -7.91882455e-01 -7.02363253e-01
  1.69334888e+00  8.14903975e-01 -4.55866873e-01 -2.35561773e-01
 -2.89508279e-07 -6.99963033e-01 -1.21276236e+00 -3.59733731e-01
 -1.43177390e-01 -6.35321

INFO:__main__:Upsert response: {'upserted_count': 1}


[ 5.44891022e-02  6.16095662e-01  1.79071784e-01 -2.73519367e-01
  6.35110974e-01 -9.60564837e-02  4.81438518e-01 -3.31754386e-01
  1.43976128e-02 -1.12035722e-02  3.01065445e-01  3.63643825e-01
  7.77894199e-01  7.24371552e-01 -5.22060633e-01  5.52789867e-01
 -2.91989416e-01  2.73989886e-01  1.23769185e-02  5.50898686e-02
 -5.91787398e-01 -6.36077821e-01  1.57262385e-01  1.23926818e+00
  7.74691641e-01  1.34754670e+00  4.31182295e-01 -4.31831032e-01
 -7.81849384e-01  1.83026642e-01  3.77799988e-01 -2.91527480e-01
 -1.16801664e-01 -4.37206864e-01  1.17949009e+00  3.50855023e-01
 -6.75028026e-01  6.72663569e-01 -7.58031160e-02 -6.53789461e-01
 -5.30276120e-01 -6.47744119e-01  3.93849462e-01  2.95071155e-01
 -1.16779387e+00 -5.06353043e-02 -1.88763335e-01  7.19263971e-01
 -5.87830469e-02  4.39498946e-02  1.38672426e-01 -7.63659120e-01
  1.07421649e+00  2.76307493e-01 -4.74184066e-01  4.27692421e-02
  3.47976363e-03 -5.24490595e-01 -1.00858772e+00 -4.08222854e-01
 -4.21891630e-01 -3.95409

INFO:__main__:Upsert response: {'upserted_count': 1}


[-3.36036831e-01  6.65800750e-01  2.53437370e-01  2.17186570e-01
 -1.33953497e-01 -3.83245260e-01  4.71733063e-01  4.45781708e-01
  1.57743916e-01  3.76097828e-01 -1.03572130e-01  7.27705061e-02
  4.34056550e-01  6.91955090e-01 -2.81964671e-02  6.91713274e-01
 -4.16016430e-01  3.44431512e-02 -6.34575710e-02 -1.43616155e-01
 -2.15129569e-01 -2.85650134e-01 -2.93145061e-01  2.91400522e-01
  6.47515178e-01  9.42857981e-01  2.51352012e-01 -1.23537207e+00
 -5.84036231e-01 -2.68134713e-01 -3.20774704e-01  1.27083167e-01
 -8.16746891e-01 -3.59690875e-01  1.66424423e-01  8.26056376e-02
 -5.52476525e-01  2.97189683e-01  4.22837995e-02  2.50945181e-01
  3.99265260e-01 -3.38377208e-01 -4.49377298e-03  1.24775462e-01
 -8.90627384e-01 -4.45471138e-01  6.92291021e-01  4.87808943e-01
 -5.03770858e-02 -1.88204527e-01  1.73494771e-01  5.43991804e-01
  7.86181629e-01  1.88286975e-01 -1.31794095e-01  7.94494331e-01
  7.10856020e-01 -9.40220892e-01 -4.81754184e-01 -4.58583981e-01
 -3.82325023e-01 -7.86157

...

INFO:__main__:Upsert response: {'upserted_count': 1}


[ 0.08673903  0.1254617  -0.1251107  -0.21184464  0.11743502  0.05431836
  0.43014023 -0.4490824   0.21911485 -0.49236047  0.5862477   0.06078765
  0.7165828   0.800651   -0.44435713  0.57293683 -0.09304794 -0.19457471
 -0.02791358  0.14448994 -0.31149128 -0.75251263  0.7119107   0.8729758
  0.3546978   1.3971993   0.2694422  -0.17510961 -0.09072588  0.307741
  0.25878298 -0.4308628  -0.2474341  -0.16730253  0.83100176  0.02718262
 -0.05975884  0.8779912   0.4176065  -0.38891423 -0.88943785 -0.82688063
  0.11951474  0.5658055  -0.6591427  -0.3095782  -0.71057177  0.60644627
  0.02725217  0.08936147 -0.7788889  -0.10977597  2.0159767   0.46739852
 -0.6241968   0.19469254  0.04029763 -0.7388122  -1.3694643  -0.38163725
 -0.492866    0.00461547 -0.00921978  0.19290371  0.31592718  0.25126186
  0.6122138  -0.02561831 -0.7512147  -0.44258332 -0.38661635 -0.6134205
 -0.7709708   0.46874323 -0.24582057 -0.75166446  0.4659358   0.03302562
  1.555528    0.46029925 -0.25110665 -0.03228915  0.250

INFO:__main__:Upsert response: {'upserted_count': 1}


[-0.1221624   0.74900305  0.22640309  0.39323753  0.5397639  -0.7852615
  0.27588293  0.7602605   0.17806144  0.14976504 -0.10591814  0.10587884
  0.563992    0.82230854 -0.19611232  0.33203262 -0.7811654   0.45372668
 -0.07750227 -0.08833549 -0.4940807  -0.625945   -0.07644343  0.71088505
  0.84405476  1.0354822   0.34364992 -1.0013244  -1.1884995   0.04884518
 -0.04559966 -0.6310677  -0.095382   -0.41593814  0.71194285  0.119279
 -1.089308    0.40631872  0.07590915 -0.10425562  0.02755465 -0.4649144
  0.5579479   0.15660842 -1.4115704  -0.16617931  0.42947224  0.752614
 -0.02212823 -0.27448046 -0.10175377  0.39772877  0.7091344   0.18148093
 -0.08340849  0.21723033  0.0855104  -0.97401327 -0.62391    -0.08621821
 -0.07581809 -0.05670543  0.05181579  0.66804457 -0.42773747  0.37815163
  0.636353    0.06237197 -0.80677044 -0.06538633  0.16981293 -0.6296876
 -0.9123665   0.4479747  -0.2355465  -0.19545802 -0.31568104  0.6740079
  0.9403635   0.50743     0.11647838 -0.10050024  0.7955127

INFO:__main__:Upsert response: {'upserted_count': 1}


Inserting tables into vectorstore

In [232]:
table_embedding = []
for i in table_summaries:
    print(i)
    table_embedding.append(get_embedding(i))

Error generating Q&A from table.


Batches: 100%|██████████| 1/1 [00:00<00:00,  1.14it/s]


Error generating Q&A from table.


Batches: 100%|██████████| 1/1 [00:00<00:00, 59.62it/s]


Error generating Q&A from table.


...

Batches: 100%|██████████| 1/1 [00:00<00:00, 73.95it/s]


Q: What is the summary of this table? A: Drugs and Cosmetics Act 1940 and Drugs and Cosmetics
Rules,; Employees State Insurance Act; National Family Planning Programme; National Malaria Eradication Programme; National Filaria Control Programme; National Leprosy Control Programme; The Maternity Benefit Act; National Small Pox Eradication Programme; National TB Control Programme; National Goitre Control Programme; National Trachoma Control Programme; Indian Medical Council Act 1933; The Contract Labour (Regulation and Adoption) Act; The Medical Termination of Pregnancy Act 1971, revised
in 1975, amended in 2002; The Integrated Child Development Services Scheme; National Blindness Control Programme; National Cancer Control Programme, revised in 2004; Family Welfare Programme; Expanded Programme of Immunisation; National Iodine Deficiency Disorder (IDD) Control
Programme; National Diabetes Control Programme
Q: What are the key findings? A: Drugs and Cosmetics Act 1940 and Drugs and Cosmeti

Batches: 100%|██████████| 1/1 [00:00<00:00, 56.84it/s]


Q: What is the summary of this table? A: National Mental Health Programme; National Leprosy Eradication Programme; National Programme for Guinea Worm Eradication; National AIDS Control Programme; The Mental Health Act; Revised National TB Control Programme; National Nutrition Policy; Persons with Disabilities (Equal Opportunities, Protection
of Rights and Full Participation) Act; Reproductive and Child Health Programme; Standards for Male and Female Sterilisation; National Policy for the Empowerment of Women; National Population Policy; National AIDS Control and Prevention Policy; National Blood Policy; National Health Policy; National Common Minimum Programme; Pre-Conception and Pre-Natal Diagnostic Techniques
(Prohibition of Sex Selection) or PC & PNDT Act; The Draft National Rural Employment Guarantee Act; Food Safety and Standards Bill; The Right to Information Act; The Communal Violence (Prevention, Control and
Rehabilitation of Victims) Bill; The HIV/AIDS Bill; National Rural Hea

Batches: 100%|██████████| 1/1 [00:00<00:00, 69.00it/s]


In [231]:
table_metadata_lst = []
for i, text in enumerate(data['tables']):
    table_metadata = data['table_metadata'][i]
    table_metadata_lst.append(table_metadata)
    print(table_metadata)

{'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf', 'page_number': 1, 'table_size': 5}
{'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf', 'page_number': 16, 'table_size': 1}
{'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf', 'page_number': 20, 'table_size': 9}
{'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf', 'page_number': 22, 'table_size': 5}
{'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf', 'page_number': 47, 'table_size': 3}
{'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf', 'page_number': 48, 'table_size': 3}
{'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf', 'page_number': 57, 'table_size': 3}
{'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf', 'page_number': 76, 'table_size': 2}
{'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf', 'page_number': 92, 'table_size': 6}
{'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf', 'page_number': 93, 'table_size': 8}
{'source_fi

In [233]:
for i in range(len(table_metadata_lst)):
    if table_embedding[i] is not None:
        print(table_embedding[i])
        try:
            response = index.upsert(
                vectors=[
                    {
                        'id': f"table_{i}",
                        'values': table_embedding[i].tolist(),
                        'metadata': table_metadata_lst[i]
                    }
                ]
            )
            logger.info(f"Upsert response: {response}")
        except Exception as e:
            logger.error(f"Error upserting table data for ")
    else:
        logger.warning(f"Embedding for table on page is None")

[-6.58276916e-01  9.90170658e-01  8.09934258e-01  6.44607320e-02
  3.35138500e-01  5.21162391e-01  7.90933788e-01  1.41526103e-01
  2.68430382e-01  4.35656697e-01 -6.24016643e-01  1.00538537e-01
  6.58445656e-02  2.17347100e-01 -5.12911439e-01 -4.03130800e-02
 -3.35944027e-01 -4.39978033e-01  8.25471878e-01 -3.56748015e-01
  2.78350890e-01  2.70266235e-01 -9.91112113e-01 -3.68241876e-01
  2.18218327e-01 -1.25193715e-01 -1.40310451e-01 -4.18521881e-01
 -1.18946266e+00 -3.68873209e-01 -1.01884887e-01 -7.03790635e-02
  8.93422484e-01 -9.18336689e-01 -8.12474251e-01  3.40261430e-01
  8.81106377e-01  9.77449119e-03  2.91699737e-01  5.04555702e-01
  2.55167007e-01  3.66593003e-01  1.12127721e+00  1.08130407e+00
 -1.28396824e-01 -4.82407659e-01 -4.91849840e-01  6.17865682e-01
  3.53888929e-01 -1.90601900e-01 -7.79208183e-01  1.01852453e+00
  1.02410293e+00  1.22384691e+00 -5.16539395e-01  6.33848682e-02
  8.97051215e-01 -1.20266461e+00  1.56102389e-01 -3.90566550e-02
 -2.32016176e-01  9.55371

INFO:__main__:Upsert response: {'upserted_count': 1}


[-6.58276916e-01  9.90170658e-01  8.09934258e-01  6.44607320e-02
  3.35138500e-01  5.21162391e-01  7.90933788e-01  1.41526103e-01
  2.68430382e-01  4.35656697e-01 -6.24016643e-01  1.00538537e-01
  6.58445656e-02  2.17347100e-01 -5.12911439e-01 -4.03130800e-02
 -3.35944027e-01 -4.39978033e-01  8.25471878e-01 -3.56748015e-01
  2.78350890e-01  2.70266235e-01 -9.91112113e-01 -3.68241876e-01
  2.18218327e-01 -1.25193715e-01 -1.40310451e-01 -4.18521881e-01
 -1.18946266e+00 -3.68873209e-01 -1.01884887e-01 -7.03790635e-02
  8.93422484e-01 -9.18336689e-01 -8.12474251e-01  3.40261430e-01
  8.81106377e-01  9.77449119e-03  2.91699737e-01  5.04555702e-01
  2.55167007e-01  3.66593003e-01  1.12127721e+00  1.08130407e+00
 -1.28396824e-01 -4.82407659e-01 -4.91849840e-01  6.17865682e-01
  3.53888929e-01 -1.90601900e-01 -7.79208183e-01  1.01852453e+00
  1.02410293e+00  1.22384691e+00 -5.16539395e-01  6.33848682e-02
  8.97051215e-01 -1.20266461e+00  1.56102389e-01 -3.90566550e-02
 -2.32016176e-01  9.55371

INFO:__main__:Upsert response: {'upserted_count': 1}


[-6.58276916e-01  9.90170658e-01  8.09934258e-01  6.44607320e-02
  3.35138500e-01  5.21162391e-01  7.90933788e-01  1.41526103e-01
  2.68430382e-01  4.35656697e-01 -6.24016643e-01  1.00538537e-01
  6.58445656e-02  2.17347100e-01 -5.12911439e-01 -4.03130800e-02
 -3.35944027e-01 -4.39978033e-01  8.25471878e-01 -3.56748015e-01
  2.78350890e-01  2.70266235e-01 -9.91112113e-01 -3.68241876e-01
  2.18218327e-01 -1.25193715e-01 -1.40310451e-01 -4.18521881e-01
 -1.18946266e+00 -3.68873209e-01 -1.01884887e-01 -7.03790635e-02
  8.93422484e-01 -9.18336689e-01 -8.12474251e-01  3.40261430e-01
  8.81106377e-01  9.77449119e-03  2.91699737e-01  5.04555702e-01
  2.55167007e-01  3.66593003e-01  1.12127721e+00  1.08130407e+00
 -1.28396824e-01 -4.82407659e-01 -4.91849840e-01  6.17865682e-01
  3.53888929e-01 -1.90601900e-01 -7.79208183e-01  1.01852453e+00
  1.02410293e+00  1.22384691e+00 -5.16539395e-01  6.33848682e-02
  8.97051215e-01 -1.20266461e+00  1.56102389e-01 -3.90566550e-02
 -2.32016176e-01  9.55371

...

INFO:__main__:Upsert response: {'upserted_count': 1}


[-6.92051053e-01  5.11259735e-01 -2.95143008e-01 -2.11601242e-01
  1.01839137e+00  9.70226340e-03 -1.22336522e-01 -3.42083871e-01
  4.80332933e-02 -2.78801143e-01  2.24748313e-01  5.80379963e-01
  4.26434398e-01  8.35778475e-01 -6.21989727e-01  1.08263850e+00
 -4.59380805e-01  2.91967392e-01  1.17348120e-01  1.86571553e-01
 -4.14263397e-01 -3.51831764e-01  1.50127962e-01  8.90678704e-01
  9.90013540e-01  1.06209159e+00  6.21594787e-01 -1.06512263e-01
 -7.21709132e-01  2.16132849e-02 -2.05788791e-01 -9.08500701e-02
  8.04257616e-02 -2.34094352e-01  2.45282441e-01  1.90385073e-01
 -2.16320515e-01  3.56419683e-01  3.07584465e-01 -3.00669432e-01
 -5.77539384e-01  1.15889817e-01 -1.57153174e-01 -8.89815167e-02
 -9.15694952e-01 -1.51097894e-01 -7.54586697e-01  5.88621616e-01
  4.68519509e-01 -4.68491435e-01  1.52316868e-01 -2.02509314e-01
  1.00554156e+00 -1.24854043e-01 -3.07024121e-01  2.77406164e-03
  2.63677053e-02 -5.56207538e-01 -9.98964071e-01 -2.24209338e-01
 -1.01981616e+00  2.36051

INFO:__main__:Upsert response: {'upserted_count': 1}


[-4.82452244e-01  3.94334674e-01 -3.54940951e-01 -1.74031630e-01
  8.48625779e-01  3.69537771e-01  9.18904170e-02 -7.36241162e-01
 -2.22293094e-01 -4.11897928e-01  4.62444305e-01  8.00497413e-01
  4.61747378e-01  7.85158336e-01 -3.55231524e-01  7.33407199e-01
 -2.12521657e-01 -1.80287864e-02  1.26786262e-01  1.23580888e-01
 -6.93180919e-01 -8.84001106e-02 -4.79460470e-02  5.89498401e-01
  1.03023875e+00  1.48928142e+00  4.81635064e-01 -2.18415231e-01
 -5.04120588e-01 -1.92467749e-01  1.64368600e-01 -2.87122190e-01
 -3.75622809e-01 -8.45022872e-02  1.00832395e-01  3.55478704e-01
 -2.31867731e-01  6.58927917e-01  5.87831795e-01  4.72188741e-02
 -6.68468475e-01 -2.11915642e-01  3.55854966e-02  1.88313067e-01
 -8.20257127e-01 -2.40324080e-01 -5.69638610e-01  2.76912272e-01
  2.64283538e-01 -2.37875536e-01 -1.99269831e-01 -2.67734885e-01
  1.26229894e+00 -7.65539939e-03 -1.98491931e-01 -2.03876495e-01
  2.22377121e-01 -5.41510761e-01 -1.09727275e+00 -6.12240911e-01
 -1.08339930e+00 -9.92174

INFO:__main__:Upsert response: {'upserted_count': 1}


inserting images into vectorstore

In [235]:
image_embedding = []
for i in image_summaries:
    print(i)
    image_embedding.append(get_embedding(i))

You are an assistant tasked with summarizing images for retrieval. These summaries will be embedded and used to retrieve the raw image. Give a concise summary of the image that is well optimized for retrieval.

0 2


Batches: 100%|██████████| 1/1 [00:00<00:00,  1.14it/s]


You are an assistant tasked with summarizing images for retrieval. These summaries will be embedded and used to retrieve the raw image. Give a concise summary of the image that is well optimized for retrieval.

0 2


Batches: 100%|██████████| 1/1 [00:00<00:00, 55.82it/s]


You are an assistant tasked with summarizing images for retrieval. These summaries will be embedded and used to retrieve the raw image. Give a concise summary of the image that is well optimized for retrieval.

2 9


...

Batches: 100%|██████████| 1/1 [00:00<00:00, 76.45it/s]


You are an assistant tasked with summarizing images for retrieval. These summaries will be embedded and used to retrieve the raw image. Give a concise summary of the image that is well optimized for retrieval.

NCAA


Batches: 100%|██████████| 1/1 [00:00<00:00, 30.04it/s]


You are an assistant tasked with summarizing images for retrieval. These summaries will be embedded and used to retrieve the raw image. Give a concise summary of the image that is well optimized for retrieval.

Other names.


Batches: 100%|██████████| 1/1 [00:00<00:00, 62.95it/s]


In [236]:
image_metadata_lst = []
for i, text in enumerate(data['images']):
    image_metadata = data['image_metadata'][i]
    image_metadata_lst.append(image_metadata)
    print(image_metadata)

{'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf', 'page_number': 1, 'image_name': 'image_page1_0_Womens.png'}
{'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf', 'page_number': 1, 'image_name': 'image_page1_1_Womens.jpeg'}
{'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf', 'page_number': 2, 'image_name': 'image_page2_0_Womens.png'}
{'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf', 'page_number': 7, 'image_name': 'image_page7_0_Womens.png'}
{'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf', 'page_number': 9, 'image_name': 'image_page9_0_Womens.png'}
{'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf', 'page_number': 145, 'image_name': 'image_page145_0_Womens.png'}


In [237]:
for i in range(len(image_metadata_lst)):
    if image_embedding[i] is not None:
        print(image_embedding[i])
        try:
            response = index.upsert(
                vectors=[
                    {
                        'id': f"image_{i}",
                        'values': image_embedding[i].tolist(),
                        'metadata': image_metadata_lst[i]
                    }
                ]
            )
            logger.info(f"Upsert response: {response}")
        except Exception as e:
            logger.error(f"Error upserting image data for ")
    else:
        logger.warning(f"Embedding for image on page is None")

[-3.89705122e-01  8.75380486e-02  1.99927366e+00  5.23485124e-01
  3.29069436e-01 -2.92966187e-01 -3.74105036e-01  9.04939994e-02
  6.66595936e-01 -6.42204523e-01  2.33049467e-01  5.92577457e-01
  1.55310273e-01 -1.54583126e-01 -4.64549303e-01  2.77049959e-01
 -3.18772733e-01 -5.50765693e-01  1.62722126e-01 -2.78634071e-01
 -1.84760898e-01 -7.44498193e-01 -4.40031081e-01  4.57743853e-01
  2.20009297e-01  5.04522026e-01 -3.85984778e-01  9.50850010e-01
 -4.82422292e-01  1.74893551e-02 -5.39643526e-01 -9.67270970e-01
  2.46487051e-01 -5.05181968e-01 -8.48220102e-03  1.36532998e+00
  8.02811742e-01  7.57616341e-01  5.67019880e-01  3.58735532e-01
 -9.29387867e-01  2.47132167e-01  7.76571929e-01  1.11179791e-01
 -1.00157428e+00 -5.90561211e-01 -5.35533726e-01  2.23569945e-01
 -1.03938602e-01 -3.53398293e-01 -6.12787724e-01  5.26501179e-01
 -4.94803846e-01  4.66129690e-01 -7.75985181e-01  1.05666578e+00
  2.25966156e-01 -1.79666948e+00 -6.30598962e-01  3.74686718e-01
 -9.34544623e-01 -1.98494

INFO:__main__:Upsert response: {'upserted_count': 1}


[-3.89705122e-01  8.75380486e-02  1.99927366e+00  5.23485124e-01
  3.29069436e-01 -2.92966187e-01 -3.74105036e-01  9.04939994e-02
  6.66595936e-01 -6.42204523e-01  2.33049467e-01  5.92577457e-01
  1.55310273e-01 -1.54583126e-01 -4.64549303e-01  2.77049959e-01
 -3.18772733e-01 -5.50765693e-01  1.62722126e-01 -2.78634071e-01
 -1.84760898e-01 -7.44498193e-01 -4.40031081e-01  4.57743853e-01
  2.20009297e-01  5.04522026e-01 -3.85984778e-01  9.50850010e-01
 -4.82422292e-01  1.74893551e-02 -5.39643526e-01 -9.67270970e-01
  2.46487051e-01 -5.05181968e-01 -8.48220102e-03  1.36532998e+00
  8.02811742e-01  7.57616341e-01  5.67019880e-01  3.58735532e-01
 -9.29387867e-01  2.47132167e-01  7.76571929e-01  1.11179791e-01
 -1.00157428e+00 -5.90561211e-01 -5.35533726e-01  2.23569945e-01
 -1.03938602e-01 -3.53398293e-01 -6.12787724e-01  5.26501179e-01
 -4.94803846e-01  4.66129690e-01 -7.75985181e-01  1.05666578e+00
  2.25966156e-01 -1.79666948e+00 -6.30598962e-01  3.74686718e-01
 -9.34544623e-01 -1.98494

INFO:__main__:Upsert response: {'upserted_count': 1}


[-0.4390475   0.01860882  2.0493102   0.55663043  0.5202492  -0.20598061
 -0.52417845  0.31794405  0.51952666 -0.72036743  0.25921378  0.46308026
  0.16813469 -0.2405093  -0.5558042   0.3692427  -0.2510038  -0.6256998
  0.08685494 -0.36567152 -0.12814744 -0.93627036 -0.2797004   0.52431023
  0.15238556  0.45953092 -0.5265459   1.0690044  -0.4808488   0.18157874
 -0.6301206  -0.9361888   0.19147639 -0.52799356 -0.09356636  1.3678112
  0.812546    0.8380264   0.49962538  0.4719372  -0.7191787   0.1636924
  0.7258849   0.06227472 -1.0477841  -0.49779165 -0.5030036   0.14374198
 -0.05020158 -0.43615684 -0.565393    0.6082599  -0.68499225  0.45938578
 -0.7059052   1.1248211   0.22904474 -1.673228   -0.7013718   0.36773565
 -1.1727016  -0.12086416  0.7033332   0.3504335   0.12507103 -0.07721815
  0.18372765 -0.7199653  -0.9032915  -0.58180165  0.08680438 -0.09733247
 -0.53258854  0.6451041  -1.131849   -0.5198016   0.14219119  0.26641083
  0.9053098   0.71993214 -0.24456751  0.10036355  0.65

...

INFO:__main__:Upsert response: {'upserted_count': 1}


[-3.59658152e-01  1.95780233e-01  1.93572199e+00  8.58189583e-01
  4.71924067e-01 -4.76808876e-01 -5.98993838e-01  2.98764795e-01
  6.27496302e-01 -8.74255836e-01  2.99093843e-01  6.03071034e-01
  2.57033110e-01 -6.48048744e-02 -2.53921807e-01  2.45230317e-01
 -2.68367082e-01 -5.27324855e-01  3.10924083e-01 -2.08632037e-01
 -4.13068742e-01 -9.04486477e-01 -3.24804515e-01  4.90781546e-01
  2.91025698e-01  8.84608269e-01 -2.98200518e-01  6.35179818e-01
 -5.38710594e-01  1.46639124e-01 -5.42195559e-01 -8.41245651e-01
  1.08809292e-01 -5.17876148e-01 -1.02096885e-01  1.40184164e+00
  9.99884129e-01  9.80352223e-01  5.25266111e-01  4.40753102e-01
 -1.12835538e+00  8.18480849e-02  4.84000355e-01  4.09686454e-02
 -1.10979474e+00 -6.51407182e-01 -4.42035824e-01  2.60039926e-01
 -2.23612234e-01 -1.79766834e-01 -4.53347772e-01  7.06136227e-01
 -8.10156107e-01  3.50758344e-01 -7.49377251e-01  9.41291869e-01
  3.00598502e-01 -1.90784204e+00 -6.13673866e-01 -5.67015596e-02
 -1.28954971e+00  9.07193

INFO:__main__:Upsert response: {'upserted_count': 1}


[-2.57427722e-01  6.59396425e-02  2.01755333e+00  5.34193754e-01
  3.78910035e-01 -2.95460582e-01 -5.77948332e-01 -4.44860198e-03
  6.22975469e-01 -6.36172891e-01  3.44048738e-01  5.99062681e-01
  1.17690235e-01 -1.95726529e-02 -5.74069500e-01  2.87506938e-01
 -3.85818332e-01 -5.36080658e-01  2.10273191e-01 -2.65603065e-01
 -1.65894300e-01 -7.01699972e-01 -3.76576006e-01  3.10742289e-01
  2.71160215e-01  5.80353975e-01 -4.08592999e-01  9.13895667e-01
 -5.12081861e-01  2.67349128e-02 -5.04076004e-01 -8.86101484e-01
  1.51043490e-01 -4.43009019e-01 -1.88154683e-01  1.31195831e+00
  8.75539064e-01  7.36974657e-01  5.40433228e-01  2.31828958e-01
 -8.42389047e-01  2.12783277e-01  7.74978638e-01  2.91925579e-01
 -9.17432427e-01 -6.27198160e-01 -4.97696310e-01  2.90070087e-01
 -2.44305551e-01 -2.74966508e-01 -6.51879549e-01  4.88108128e-01
 -5.51638067e-01  4.60679650e-01 -6.55360937e-01  1.01316226e+00
  2.06553027e-01 -1.85243499e+00 -6.01418614e-01  3.51147413e-01
 -1.02815807e+00 -2.27803

INFO:__main__:Upsert response: {'upserted_count': 1}


In [196]:
from sentence_transformers import SentenceTransformer
import logging
import pinecone

# Initialize logging
logging.basicConfig(level=logging.INFO)
logger = logging.getLogger(__name__)

# Initialize the model

def insert_data_into_pinecone1(index, pdf_data, image_summaries, table_summaries, text_chunk_list):
    for data in pdf_data:
        filename = data['filename']
        try:
            # Insert text data
            for i, text in enumerate(data['texts']):
                text_metadata = data['text_metadata'][i]
                text = data['text'][i]
                logger.info(f"Processing text: {text[:30]}... with metadata: {text_metadata}")

                embedding = get_embedding(text)
                if embedding is not None:
                    try:
                        response = index.upsert(
                            vectors=[
                                {
                                    'id': f"{filename}_text_{text_metadata['page_number']}_{i}",
                                    'values': embedding.tolist(),
                                    'metadata': text_metadata
                                }
                            ]
                        )
                        logger.info(f"Upsert response: {response}")
                    except Exception as e:
                        logger.error(f"Error upserting text data for {filename} on page {text_metadata['page_number']}. Error: {e}")
                else:
                    logger.warning(f"Embedding for text on page {text_metadata['page_number']} is None")


        except Exception as e:
            logger.error(f"Error processing file {filename}. Error: {e}")

INFO:sentence_transformers.SentenceTransformer:Use pytorch device_name: mps
INFO:sentence_transformers.SentenceTransformer:Load pretrained SentenceTransformer: bert-base-nli-mean-tokens
/Users/dhvani/Desktop/blossombot/.venv/lib/python3.11/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


In [190]:
from sentence_transformers import SentenceTransformer
import logging
import pinecone

# Initialize logging
logging.basicConfig(level=logging.INFO)
logger = logging.getLogger(__name__)

# Initialize the model
model = SentenceTransformer('bert-base-nli-mean-tokens')

def get_embedding(text):
    try:
        embedding = model.encode(text)
        return embedding
    except Exception as e:
        logger.error(f"Error generating embedding for text: {text}. Error: {e}")
        return None

def insert_data_into_pinecone(index, pdf_data, image_summaries, table_summaries, text_chunk_list):
    for data in pdf_data:
        filename = data['filename']
        try:
            # Insert text data
            for i, text in enumerate(data['texts']):
                text_metadata = data['text_metadata'][i]
                text = text_chunk_list[i]
                logger.info(f"Processing text: {text[:30]}... with metadata: {text_metadata}")

                embedding = get_embedding(text)
                if embedding is not None:
                    try:
                        response = index.upsert(
                            vectors=[
                                {
                                    'id': f"{filename}_text_{text_metadata['page_number']}_{i}",
                                    'values': embedding.tolist(),
                                    'metadata': text_metadata
                                }
                            ]
                        )
                        logger.info(f"Upsert response: {response}")
                    except Exception as e:
                        logger.error(f"Error upserting text data for {filename} on page {text_metadata['page_number']}. Error: {e}")
                else:
                    logger.warning(f"Embedding for text on page {text_metadata['page_number']} is None")

            # Insert table summaries
            for i, table in enumerate(data['tables']):
                table_metadata = data['table_metadata'][i]
                table_summary = table_summaries[i] or ""  # Handle NoneType summary
                logger.info(f"Processing table summary with metadata: {table_metadata}")

                embedding = get_embedding(table_summary)
                if embedding is not None:
                    try:
                        response = index.upsert(
                            vectors=[
                                {
                                    'id': f"{filename}_table_{table_metadata['page_number']}_{i}",
                                    'values': embedding.tolist(),
                                    'metadata': table_metadata
                                }
                            ]
                        )
                        logger.info(f"Upsert response: {response}")
                    except Exception as e:
                        logger.error(f"Error upserting table data for {filename} on page {table_metadata['page_number']}. Error: {e}")
                else:
                    logger.warning(f"Embedding for table on page {table_metadata['page_number']} is None")

            # Insert image summaries
            for i, image in enumerate(data['images']):
                image_metadata = data['image_metadata'][i]
                image_summary = image_summaries[i] or ""  # Handle NoneType summary
                logger.info(f"Processing image summary with metadata: {image_metadata}")

                embedding = get_embedding(image_summary)
                if embedding is not None:
                    try:
                        response = index.upsert(
                            vectors=[
                                {
                                    'id': f"{filename}_image_{image_metadata['page_number']}_{i}",
                                    'values': embedding.tolist(),
                                    'metadata': image_metadata
                                }
                            ]
                        )
                        logger.info(f"Upsert response: {response}")
                    except Exception as e:
                        logger.error(f"Error upserting image data for {filename} on page {image_metadata['page_number']}. Error: {e}")
                else:
                    logger.warning(f"Embedding for image on page {image_metadata['page_number']} is None")

        except Exception as e:
            logger.error(f"Error processing file {filename}. Error: {e}")


INFO:sentence_transformers.SentenceTransformer:Use pytorch device_name: mps
INFO:sentence_transformers.SentenceTransformer:Load pretrained SentenceTransformer: bert-base-nli-mean-tokens


In [197]:
insert_data_into_pinecone1(index, pdf_data , image_summaries, table_summaries , text_chunk_list)

ERROR:__main__:Error processing file Womens.pdf. Error: 'text'


In [285]:
print(index.describe_index_stats())


{'dimension': 768,
 'index_fullness': 0.0,
 'namespaces': {'': {'vector_count': 145}},
 'total_vector_count': 145}


In [283]:
query = "what is womens health"
model1 = SentenceTransformer('bert-base-nli-mean-tokens')

query_vector = model1.encode(query).tolist()

INFO:sentence_transformers.SentenceTransformer:Use pytorch device_name: mps
INFO:sentence_transformers.SentenceTransformer:Load pretrained SentenceTransformer: bert-base-nli-mean-tokens
Batches: 100%|██████████| 1/1 [00:00<00:00, 44.64it/s]


In [284]:
a = index.query(
    namespace="",
    vector=query_vector,
    top_k=3,
    include_values=True
)

In [239]:
print(a)

{'matches': [{'id': 'text_0',
              'score': 0.780154169,
              'values': [0.471695304,
                         0.197417647,
                         0.00474661868,
                         -0.0676839724,
                         0.453341126,
                         0.01913381,
                         0.663943172,
                         -0.566610754,
                         -0.322602898,
                         -0.147070438,
                         0.745022476,
                         0.617788255,
                         0.38450104,
                         1.02253306,
                         -0.476349235,
                         0.520720959,
                         -0.426309168,
                         0.0326837488,
                         0.00355543895,
                         -0.204443336,
                         -0.445711493,
                         -0.40312168,
                         0.483097166,
                         0.322541744,
           

In [171]:
# Initialize the SentenceTransformer model (use a model with 768 dimensions)
model = SentenceTransformer('paraphrase-mpnet-base-v2')  # This model has a 768-dimensional output

def get_similar_docs(query, k=1, score=False, namespace=None):
    # Convert the text query to a vector using the embedding model
    query_vector = model.encode(query).tolist()
    
    # Perform the query using the Pinecone index with keyword arguments
    response = index.query(vector=query_vector, top_k=k, namespace= '')
    
    # Print the response to understand its structure
    print(response)
    
    if score:
        # Return both the documents and their scores
        similar_docs_with_scores = [(match['id'], match['score']) for match in response['matches']]
        return similar_docs_with_scores
    else:
        # Return only the document ids
        similar_docs = [match['id'] for match in response['matches']]
        return similar_docs

INFO:sentence_transformers.SentenceTransformer:Use pytorch device_name: mps
INFO:sentence_transformers.SentenceTransformer:Load pretrained SentenceTransformer: paraphrase-mpnet-base-v2


In [281]:
query = "what is womens health"

get_similar_docs(query, k=5, score=True, namespace='')

Batches: 100%|██████████| 1/1 [00:02<00:00,  2.89s/it]


{'matches': [{'id': 'text_0', 'score': 0.780154169, 'values': []},
             {'id': 'text_10', 'score': 0.67599231, 'values': []},
             {'id': 'text_143', 'score': 0.671126127, 'values': []},
             {'id': 'text_109', 'score': 0.664196551, 'values': []},
             {'id': 'text_3', 'score': 0.649538457, 'values': []}],
 'namespace': '',
 'usage': {'read_units': 5}}


[('text_0', 0.780154169),
 ('text_10', 0.67599231),
 ('text_143', 0.671126127),
 ('text_109', 0.664196551),
 ('text_3', 0.649538457)]

In [282]:
search_response

{'matches': [{'id': 'text_0',
              'metadata': {'chunk_size': 81.0,
                           'page_number': 1.0,
                           'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf'},
              'score': 0.780154169,
              'values': [0.471695304,
                         0.197417647,
                         0.00474661868,
                         -0.0676839724,
                         0.453341126,
                         0.01913381,
                         0.663943172,
                         -0.566610754,
                         -0.322602898,
                         -0.147070438,
                         0.745022476,
                         0.617788255,
                         0.38450104,
                         1.02253306,
                         -0.476349235,
                         0.520720959,
                         -0.426309168,
                         0.0326837488,
                         0.00355543895,
                   

In [287]:
# Combine the vectors into a single text variable for the prompt
chunks = []
search_response = index.query(vector=query_vector, top_k=5, namespace='', include_values=True, include_metadata=True)

for i, item in enumerate(search_response['matches']):
    print(item)

{'id': 'text_0',
 'metadata': {'chunk_size': 81.0,
              'original_text': 'NATIONAL HUMAN RIGHTS COMMISSION\n'
                               'Women’s Right to Health\n'
                               'N. B. Sarojini & others\n',
              'page_number': 1.0,
              'source_file': '/Users/dhvani/Desktop/blossombot/Womens.pdf'},
 'score': 0.780154169,
 'values': [0.471695304,
            0.197417647,
            0.00474661868,
            -0.0676839724,
            0.453341126,
            0.01913381,
            0.663943172,
            -0.566610754,
            -0.322602898,
            -0.147070438,
            0.745022476,
            0.617788255,
            0.38450104,
            1.02253306,
            -0.476349235,
            0.520720959,
            -0.426309168,
            0.0326837488,
            0.00355543895,
            -0.204443336,
            -0.445711493,
            -0.40312168,
            0.483097166,
            0.322541744,
            0.830

In [291]:
for i, item in enumerate(search_response['matches']):
    original_text = item['metadata']['original_text']
    print(original_text)

NATIONAL HUMAN RIGHTS COMMISSION
Women’s Right to Health
N. B. Sarojini & others

10
The second chapter focuses on the situation of women’s health in India and
examines the factors that impinge on their right to health and well being, and
locates the role of gender within these.
The third chapter documents the major campaigns that the women’s movement
undertook to ensure protection of women’s health rights. A brief account of the
alternative activities initiated by diverse women’s networks and health groups
towards comprehensive health care, and particularly women’s health, has also
been presented in this section.
The fourth chapter looks into the national and international instruments that
have emerged over the years. Some of these provisions and Acts are the product
of constant struggles staged by the women’s and the health movements.
And finally, the last chapter provides action agendas, strategies which have
been/can be adopted around the issue of health at different levels. It set

In [294]:
chunks = []
for i, item in enumerate(search_response['matches']):
    content = item['values']
    metadata = item['metadata']
    original_text = metadata.get('original_text')  # Get original_text from metadata if it exists
    print("\n\n\n")
    print(i)
    print(original_text)





0
NATIONAL HUMAN RIGHTS COMMISSION
Women’s Right to Health
N. B. Sarojini & others





1
10
The second chapter focuses on the situation of women’s health in India and
examines the factors that impinge on their right to health and well being, and
locates the role of gender within these.
The third chapter documents the major campaigns that the women’s movement
undertook to ensure protection of women’s health rights. A brief account of the
alternative activities initiated by diverse women’s networks and health groups
towards comprehensive health care, and particularly women’s health, has also
been presented in this section.
The fourth chapter looks into the national and international instruments that
have emerged over the years. Some of these provisions and Acts are the product
of constant struggles staged by the women’s and the health movements.
And finally, the last chapter provides action agendas, strategies which have
been/can be adopted around the issue of health at different le

In [311]:
import spacy
nlp = spacy.load("en_core_web_sm")
#nlp = spacy.load("en_pipeline")

In [300]:
import pandas as pd
from langkit import extract, pii
import whylogs as why
from langkit import light_metrics

llm_schema = light_metrics.init()


# Define a function to extract information from a single row of the dataframe
def extract_info_eng(query, answer):
    data = {"prompt": query,
            "response": answer}
    result = extract(data)
    return result

INFO:langkit.pattern_loader:Loaded regex pattern for SSN
INFO:langkit.pattern_loader:Loaded regex pattern for credit card number
INFO:langkit.pattern_loader:Loaded regex pattern for phone number
INFO:langkit.pattern_loader:Loaded regex pattern for mailing address
INFO:langkit.pattern_loader:Loaded regex pattern for email address
INFO:langkit.pattern_loader:Loaded regex pattern for SSN
INFO:langkit.pattern_loader:Loaded regex pattern for credit card number
INFO:langkit.pattern_loader:Loaded regex pattern for phone number
INFO:langkit.pattern_loader:Loaded regex pattern for mailing address
INFO:langkit.pattern_loader:Loaded regex pattern for email address


In [323]:
query =" hi how are you?"
answer = "i am fine"
result = extract_info_eng(query, answer)

In [324]:
df1 = pd.DataFrame(result.items())

In [325]:
print(df1)

                                       0                 1
0                                 prompt   hi how are you?
1                               response         i am fine
2             prompt.pii_presidio.result                []
3     prompt.pii_presidio.entities_count                 0
4           response.pii_presidio.result                []
5   response.pii_presidio.entities_count                 0
6             prompt.flesch_reading_ease            118.18
7           response.flesch_reading_ease            119.19
8     prompt.automated_readability_index              -5.4
9   response.automated_readability_index              -9.1
10        prompt.aggregate_reading_level               0.0
11      response.aggregate_reading_level               1.0
12                 prompt.syllable_count                 4
13               response.syllable_count                 3
14                  prompt.lexicon_count                 4
15                response.lexicon_count                

In [315]:
# Transpose the DataFrame
transposed_df = df1.T

In [316]:
transposed_df

0          1                           2   \
0            prompt   response  prompt.pii_presidio.result   
1   hi how are you?  i am fine                          []   

                                   3                             4   \
0  prompt.pii_presidio.entities_count  response.pii_presidio.result   
1                                   0                            []   

                                     5                           6   \
0  response.pii_presidio.entities_count  prompt.flesch_reading_ease   
1                                     0                      118.18   

                             7                                   8   \
0  response.flesch_reading_ease  prompt.automated_readability_index   
1                        119.19                                -5.4   

                                     9   ...                   20  \
0  response.automated_readability_index  ...  prompt.letter_count   
1                                  -9.1  ...                   11   

                      21                         22  \
0  response.letter_count  prompt.polysyllable_count   
1                      7                          0   

                            23                         24  \
0  response.polysyllable_count  prompt.monosyllable_count   
1                            0                          4   

                            25                      26  \
0  response.monosyllable_count  prompt.difficult_words   
1                            3                       0   

                         27                   28                     29  
0  response.difficult_words  prompt.has_patterns  response.has_patterns  
1                         0                 None                   None  

[2 rows x 30 columns]

In [319]:
print(transposed_df.columns)

RangeIndex(start=0, stop=30, step=1)


In [326]:
transposed_df.reset_index(drop=True, inplace=True)


In [327]:
print(transposed_df)

                 0          1                           2   \
0            prompt   response  prompt.pii_presidio.result   
1   hi how are you?  i am fine                          []   

                                   3                             4   \
0  prompt.pii_presidio.entities_count  response.pii_presidio.result   
1                                   0                            []   

                                     5                           6   \
0  response.pii_presidio.entities_count  prompt.flesch_reading_ease   
1                                     0                      118.18   

                             7                                   8   \
0  response.flesch_reading_ease  prompt.automated_readability_index   
1                        119.19                                -5.4   

                                     9   ...                   20  \
0  response.automated_readability_index  ...  prompt.letter_count   
1                                